# Differential Expression Analysis (DEG) Script

This script performs **differential expression analysis** to identify cell-type–specific marker genes.

1. **Marker Detection**  
   - Differentially expressed genes (DEGs) are identified using the **`FindAllMarkers`** function.  
   - Only genes that satisfy the thresholds **adjusted p-value < 0.05** and **log2 fold change > 1** are retained.  

2. **Top Gene Selection**  
   - For each annotated cell type, the **top 20 DEGs** are selected based on significance and effect size.  
   - Genes that are not mutually exclusive (i.e., shared across multiple cell types) are removed to ensure cell-type specificity.  

3. **Visualization**  
   - For the final set of mutually exclusive DEGs, **violin plots** are generated.  
   - These plots highlight the expression patterns of selected marker genes across different cell populations, providing a clear visualization of cell-type–specific expression.  

---

In summary, the script extracts statistically significant DEGs, filters for top and mutually exclusive genes per cell type, and visualizes their distributions using violin plots.


In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [ ]:
!pip install matplotlib

In [ ]:
!pip install scanpy

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 27.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 169.1/169.1 kB 10.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.9/232.9 kB 18.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.9/56.9 kB 3.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.5/10.5 MB 99.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 90.1/90.1 kB 7.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.2/58.2 kB 4.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 255.4/255.4 kB 16.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.8/8.8 MB 134.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.7/53.7 kB 3.7 MB/s eta 0:00:00


In [ ]:
import numpy as np
import pandas as pd
import scanpy as sc
import anndata
import os
import sys
from scipy import sparse

Creating adata and metafile

HVG

In [ ]:
import rpy2.rinterface_lib.callbacks
import logging
# Ignore R warning messages
#Note: this can be commented out to get more verbose R output
rpy2.rinterface_lib.callbacks.logger.setLevel(logging.ERROR)

%load_ext rpy2.ipython

The rpy2.ipython extension is already loaded. To reload it, use:
  %reload_ext rpy2.ipython


In [ ]:
from rpy2.robjects import conversion, default_converter

In [ ]:
with conversion.localconverter(default_converter):
  %R install.packages("BiocManager")
  %R BiocManager::install('scran')
  %R library("scran")


Installing package into ‘/usr/local/lib/R/site-library’
(as ‘lib’ is unspecified)
trying URL 'https://cran.rstudio.com/src/contrib/BiocManager_1.30.26.tar.gz'
Content type 'application/x-gzip' length 594489 bytes (580 KB)
downloaded 580 KB


The downloaded source packages are in
	‘/tmp/RtmpRmnJal/downloaded_packages’


'getOption("repos")' replaces Bioconductor standard repositories, see
'help("repositories", package = "BiocManager")' for details.
Replacement repositories:
    CRAN: https://cran.rstudio.com
Bioconductor version 3.21 (BiocManager 1.30.26), R 4.5.1 (2025-06-13)
Installing package(s) 'scran'
also installing the dependencies ‘formatR’, ‘lambda.r’, ‘futile.options’, ‘futile.logger’, ‘snow’, ‘locfit’, ‘ScaledMatrix’, ‘rsvd’, ‘assorthead’, ‘BiocNeighbors’, ‘scuttle’, ‘BiocParallel’, ‘edgeR’, ‘limma’, ‘statmod’, ‘BiocSingular’, ‘bluster’, ‘metapod’, ‘beachmat’

trying URL 'https://cran.rstudio.com/src/contrib/formatR_1.14.tar.gz'
trying URL 'https://cran.rstudio.com/src/contrib/lambda.r_1.2.4.tar.gz'
trying URL 'https://cran.rstudio.com/src/contrib/futile.options_1.0.1.tar.gz'
trying URL 'https://cran.rstudio.com/src/contrib/futile.logger_1.4.3.tar.gz'
trying URL 'https://cran.rstudio.com/src/contrib/snow_0.4-4.tar.gz'
trying URL 'https://cran.rstudio.com/src/contrib/locfit_1.5-9.12.tar.gz'


Loading required package: scuttle


In [ ]:
with conversion.localconverter(default_converter):
  %R install.packages("SingleCellExperiment")
  %R library("SingleCellExperiment")

Installing package into ‘/usr/local/lib/R/site-library’
(as ‘lib’ is unspecified)
In addition: Warning message:
package ‘SingleCellExperiment’ is not available for this version of R

A version of this package for your version of R might be available elsewhere,
see the ideas at
https://cran.r-project.org/doc/manuals/r-patched/R-admin.html#Installing-packages 


In [ ]:
df_T = df.T

In [ ]:
%R -i df_T
%R sce <- SingleCellExperiment(assays = list(logcounts=as.matrix(df_T)))

%R dec <- modelGeneVar(sce)
%R top_hvgs <- getTopHVGs(dec,n=3000) #prop=0.1 default %10 top

%R -o top_hvgs


/usr/local/lib/python3.11/dist-packages/anndata2ri/_r2py.py:129: FutureWarning: The specified parameters ('obsm',) are no longer positional. Please specify them like `obsm={}`
  return AnnData(exprs, obs, var, uns, obsm, layers=layers)


In [ ]:
df_hvg = df[top_hvgs]
df_hvg

SST      REG1A      PPY           INS      PRSS1      REG3A  \
gene                                                                           
Sample_1    0.000000   3.015700   0.0000  24994.856100  14.912300   0.000000   
Sample_2   33.395300  87.070400   0.0000  62046.692100  25.833400   0.000000   
Sample_3    0.000000   3.477100   0.0000  46114.007600   0.000000   0.000000   
Sample_4    1.253500   0.980500  12.1348  44912.259700   0.000000   0.000000   
Sample_5   29.297600   0.000000   0.0000  22104.963400   0.000000   0.000000   
...              ...        ...      ...           ...        ...        ...   
D30-8_90   70.993737   2.007853   0.0000      1.001958   1.001958   4.031579   
D30-8_91  218.580368  14.397368   0.0000      3.017717   0.000000   9.162012   
D30-8_92  160.050309   1.001958   0.0000      1.001958   1.001958  13.341696   
D30-8_93  128.448596   7.097484   0.0000      1.001958   0.000000   8.127667   
D30-8_94  207.098623   8.127667   0.0000      0.000000   0.000000  18.664133   

          CLPS      REG1B        SPP1         IAPP  ...  ANKLE1      HEY2  \
gene                                                ...                     
Sample_1   0.0   6.046300    0.000000   475.990500  ...     0.0  0.000000   
Sample_2   0.0  49.462300    0.000000  2138.593500  ...     0.0  0.000000   
Sample_3   0.0   0.000000    0.000000  4295.946500  ...     0.0  0.000000   
Sample_4   0.0   0.000000    0.000000  3361.361100  ...     0.0  0.000000   
Sample_5   0.0   0.000000    0.000000  9927.753000  ...     0.0  0.000000   
...        ...        ...         ...          ...  ...     ...       ...   
D30-8_90   0.0   2.007853    0.000000     0.000000  ...     0.0  0.000000   
D30-8_91   0.0   2.007853    1.001958     2.007853  ...     0.0  1.001958   
D30-8_92   0.0   3.017717    0.000000     3.017717  ...     0.0  0.000000   
D30-8_93   0.0   1.001958  185.573345     1.001958  ...     0.0  0.000000   
D30-8_94   0.0   1.001958    2.007853     1.001958  ...     0.0  0.000000   

          KCNJ15  VIP  LPO  CD300LF  ENPP6  SLC25A2  CYBB  CXCL9  
gene                                                              
Sample_1     0.0  0.0  0.0      0.0    0.0      0.0   0.0    0.0  
Sample_2     0.0  0.0  0.0      0.0    0.0      0.0   0.0    0.0  
Sample_3     0.0  0.0  0.0      0.0    0.0      0.0   0.0    0.0  
Sample_4     0.0  0.0  0.0      0.0    0.0      0.0   0.0    0.0  
Sample_5     0.0  0.0  0.0      0.0    0.0      0.0   0.0    0.0  
...          ...  ...  ...      ...    ...      ...   ...    ...  
D30-8_90     0.0  0.0  0.0      0.0    0.0      0.0   0.0    0.0  
D30-8_91     0.0  0.0  0.0      0.0    0.0      0.0   0.0    0.0  
D30-8_92     0.0  0.0  0.0      0.0    0.0      0.0   0.0    0.0  
D30-8_93     0.0  0.0  0.0      0.0    0.0      0.0   0.0    0.0  
D30-8_94     0.0  0.0  0.0      0.0    0.0      0.0   0.0    0.0  

[14172 rows x 2308 columns]

In [ ]:
adata_df = df_hvg

In [ ]:
metadata_df = pd.DataFrame(df_label['label'])
metadata_df.rename(columns = {'label':'cell_type'}, inplace = True)
metadata_df

cell_type
Sample_1         beta
Sample_2         beta
Sample_3         beta
Sample_4         beta
Sample_5         beta
...               ...
D30-8_90        alpha
D30-8_91  mesenchymal
D30-8_92        alpha
D30-8_93       ductal
D30-8_94  mesenchymal

[14172 rows x 1 columns]

In [ ]:
import anndata
adata = anndata.AnnData(adata_df)
adata

AnnData object with n_obs × n_vars = 14172 × 3000

In [ ]:
adata.obs = metadata_df
adata.obs

cell_type
Sample_1         beta
Sample_2         beta
Sample_3         beta
Sample_4         beta
Sample_5         beta
...               ...
D30-8_90        alpha
D30-8_91  mesenchymal
D30-8_92        alpha
D30-8_93       ductal
D30-8_94  mesenchymal

[14172 rows x 1 columns]

In [ ]:
vars = pd.DataFrame()
vars["gene_ids"] = adata_df.columns
vars.index = adata_df.columns
vars["feature_types"] = "Gene Expression"
vars

gene_ids    feature_types
GCG         GCG  Gene Expression
INS         INS  Gene Expression
TTR         TTR  Gene Expression
IAPP       IAPP  Gene Expression
REG1A     REG1A  Gene Expression
...         ...              ...
DHRS7B   DHRS7B  Gene Expression
PTGFRN   PTGFRN  Gene Expression
SEMA3B   SEMA3B  Gene Expression
PNPLA2   PNPLA2  Gene Expression
ARRDC2   ARRDC2  Gene Expression

[3000 rows x 2 columns]

In [ ]:
adata.var = vars

In [ ]:
adata.write(gdrivePath +os.sep+"Revision"+os.sep+"DGE"+os.sep+'adata.h5ad')

In [ ]:
metadata_df.to_csv(gdrivePath+os.sep+"Revision"+os.sep+"DGE"+os.sep+"metadataTest.tsv", sep = '\t')

------------------------------------------------

In [ ]:
meta_file_path = gdrivePath+os.sep+"Revision"+os.sep+"DGE"+os.sep+"metadataTest.tsv"
counts_file_path = gdrivePath +os.sep+"Revision"+os.sep+"DGE"+os.sep+'adata.h5ad'
out_path = gdrivePath +os.sep+'Revision/DGE'
cpdb_file_path = gdrivePath+os.sep+'cellphonedb'+os.sep+'data'+os.sep+cpdb_version+os.sep+'cellphonedb.zip'

In [ ]:
import anndata
adata = anndata.read_h5ad(counts_file_path)
adata

AnnData object with n_obs × n_vars = 14172 × 3000
    obs: 'cell_type'
    var: 'gene_ids', 'feature_types'

In [ ]:
adata.obs['cell_type'].values.describe()

counts     freqs
categories                          
PSC                     53  0.003740
acinar                1362  0.096105
activated_stellate     284  0.020040
alpha                 4871  0.343706
beta                  3688  0.260231
delta                  949  0.066963
ductal                1700  0.119955
endothelial            289  0.020392
epsilon                 21  0.001482
gamma                  424  0.029918
macrophage              55  0.003881
mast                    25  0.001764
mesenchymal             80  0.005645
pp                     185  0.013054
quiescent_stellate     173  0.012207
schwann                 13  0.000917

In [ ]:
df_meta = pd.DataFrame(data={'Cell':list(adata.obs.index),
                             'cell_type':[ i for i in adata.obs['cell_type']]
                            })
df_meta.set_index('Cell', inplace=True)
df_meta
#df_meta.to_csv('endometrium_example_meta.tsv', sep = '\t')

cell_type
Cell                 
Sample_1         beta
Sample_2         beta
Sample_3         beta
Sample_4         beta
Sample_5         beta
...               ...
D30-8_90        alpha
D30-8_91  mesenchymal
D30-8_92        alpha
D30-8_93       ductal
D30-8_94  mesenchymal

[14172 rows x 1 columns]

In [ ]:
# Conver to dense matrix for Seurat
#adata.X = adata.X.toarray()
type(adata.X)

numpy.ndarray

In [ ]:
!pip install anndata2ri

In [ ]:
!pip install rpy2

In [ ]:
import rpy2.rinterface_lib.callbacks
import logging
# Ignore R warning messages
#Note: this can be commented out to get more verbose R output
rpy2.rinterface_lib.callbacks.logger.setLevel(logging.ERROR)
import anndata2ri
anndata2ri.activate()
%load_ext rpy2.ipython

/tmp/ipython-input-319474481.py:7: DeprecationWarning: The global conversion available with activate() is deprecated and will be removed in the next major release. Use a local converter.
  anndata2ri.activate()


In [ ]:
import anndata2ri
from rpy2.robjects import pandas2ri
from rpy2.robjects import conversion
from rpy2.robjects.conversion import localconverter

import anndata

# Activate conversions
pandas2ri.activate()


In [ ]:
from rpy2.robjects import conversion, default_converter

In [ ]:
with conversion.localconverter(default_converter):
  %R install.packages("BiocManager")

Installing package into ‘/usr/local/lib/R/site-library’
(as ‘lib’ is unspecified)
trying URL 'https://cran.rstudio.com/src/contrib/BiocManager_1.30.26.tar.gz'
Content type 'application/x-gzip' length 594489 bytes (580 KB)
downloaded 580 KB


The downloaded source packages are in
	‘/tmp/RtmpAsW1rC/downloaded_packages’


In [ ]:
with conversion.localconverter(default_converter):
  %R BiocManager::install("S4Vectors")

Update all/some/none? [a/s/n]: a


'getOption("repos")' replaces Bioconductor standard repositories, see
'help("repositories", package = "BiocManager")' for details.
Replacement repositories:
    CRAN: https://cran.rstudio.com
Bioconductor version 3.21 (BiocManager 1.30.26), R 4.5.1 (2025-06-13)
Installing package(s) 'BiocVersion', 'S4Vectors'
also installing the dependency ‘BiocGenerics’

trying URL 'https://bioconductor.org/packages/3.21/bioc/src/contrib/BiocGenerics_0.54.0.tar.gz'
trying URL 'https://bioconductor.org/packages/3.21/bioc/src/contrib/BiocVersion_3.21.1.tar.gz'
trying URL 'https://bioconductor.org/packages/3.21/bioc/src/contrib/S4Vectors_0.46.0.tar.gz'

The downloaded source packages are in
	‘/tmp/RtmpAsW1rC/downloaded_packages’
Old packages: 'broom'
trying URL 'https://cran.rstudio.com/src/contrib/broom_1.0.9.tar.gz'
Content type 'application/x-gzip' length 651399 bytes (636 KB)
downloaded 636 KB


The downloaded source packages are in
	‘/tmp/RtmpAsW1rC/downloaded_packages’


In [ ]:
with conversion.localconverter(default_converter):
  %R BiocManager::install("SingleCellExperiment")

'getOption("repos")' replaces Bioconductor standard repositories, see
'help("repositories", package = "BiocManager")' for details.
Replacement repositories:
    CRAN: https://cran.rstudio.com
Bioconductor version 3.21 (BiocManager 1.30.26), R 4.5.1 (2025-06-13)
Installing package(s) 'SingleCellExperiment'
also installing the dependencies ‘matrixStats’, ‘UCSC.utils’, ‘GenomeInfoDbData’, ‘abind’, ‘MatrixGenerics’, ‘Biobase’, ‘IRanges’, ‘GenomeInfoDb’, ‘S4Arrays’, ‘XVector’, ‘SparseArray’, ‘SummarizedExperiment’, ‘GenomicRanges’, ‘DelayedArray’

trying URL 'https://cran.rstudio.com/src/contrib/matrixStats_1.5.0.tar.gz'
trying URL 'https://bioconductor.org/packages/3.21/bioc/src/contrib/UCSC.utils_1.4.0.tar.gz'
trying URL 'https://bioconductor.org/packages/3.21/data/annotation/src/contrib/GenomeInfoDbData_1.2.14.tar.gz'
trying URL 'https://cran.rstudio.com/src/contrib/abind_1.4-8.tar.gz'
trying URL 'https://bioconductor.org/packages/3.21/bioc/src/contrib/MatrixGenerics_1.20.0.tar.gz'
tryin

In [ ]:
with conversion.localconverter(default_converter):
  %R BiocManager::install("Seurat")

In [ ]:
with conversion.localconverter(default_converter):
  %R library(Seurat)

In [ ]:
with conversion.localconverter(default_converter):
  %R library(SingleCellExperiment)

In [ ]:
%R library(dplyr)


Attaching package: ‘dplyr’

The following objects are masked from ‘package:stats’:

    filter, lag

The following objects are masked from ‘package:base’:

    intersect, setdiff, setequal, union



In [ ]:
from rpy2.robjects import default_converter
from rpy2.robjects.conversion import localconverter

with localconverter(default_converter + anndata2ri.converter):
    %R -i adata


In [ ]:
with conversion.localconverter(default_converter):
  %R so = as.Seurat(adata, counts = "X", data = "X")

In [ ]:
with conversion.localconverter(default_converter):
  %R Idents(so) = so$cell_type

In [ ]:
with conversion.localconverter(default_converter):
  %R DEGs <- FindAllMarkers(so, test.use = 'LR', verbose = F, only.pos = T, random.seed = 1, logfc.threshold = 1, min.pct = 0.1, return.thresh = 0.05) #logfc.threshold =0.2

In addition: There were 17 warnings (use warnings() to see them)


In [ ]:
%R DEGs

p_val  avg_log2FC  pct.1  pct.2     p_val_adj  cluster    gene
COL1A2   3.061042e-67    5.610351  1.000  0.901  9.183127e-64      PSC  COL1A2
SPARC    1.969977e-66    5.698530  1.000  0.344  5.909931e-63      PSC   SPARC
LUM      1.086253e-61    6.436757  0.811  0.726  3.258758e-58      PSC     LUM
COL3A1   3.802095e-60    4.731757  1.000  0.891  1.140629e-56      PSC  COL3A1
DCN      6.263654e-59    6.115082  0.830  0.132  1.879096e-55      PSC     DCN
...               ...         ...    ...    ...           ...      ...     ...
PSMD32   4.782692e-02    1.272259  0.615  0.595  1.000000e+00  schwann   PSMD3
BAX      4.819460e-02    2.452157  0.538  0.599  1.000000e+00  schwann     BAX
PDF1     4.835998e-02    2.270163  0.231  0.333  1.000000e+00  schwann     PDF
CORO1B2  4.887975e-02    1.666829  0.538  0.576  1.000000e+00  schwann  CORO1B
INPP5F3  4.896444e-02    1.611884  1.000  0.944  1.000000e+00  schwann  INPP5F

[4831 rows x 7 columns]

In [ ]:
%R fDEGs <- DEGs[DEGs$p_val_adj < 0.05 & DEGs$avg_log2FC > 1, ]

p_val  avg_log2FC  pct.1  pct.2     p_val_adj  cluster    gene
COL1A2  3.061042e-67    5.610351  1.000  0.901  9.183127e-64      PSC  COL1A2
SPARC   1.969977e-66    5.698530  1.000  0.344  5.909931e-63      PSC   SPARC
LUM     1.086253e-61    6.436757  0.811  0.726  3.258758e-58      PSC     LUM
COL3A1  3.802095e-60    4.731757  1.000  0.891  1.140629e-56      PSC  COL3A1
DCN     6.263654e-59    6.115082  0.830  0.132  1.879096e-55      PSC     DCN
...              ...         ...    ...    ...           ...      ...     ...
CLIC46  6.399125e-06    3.293190  0.615  0.297  1.919737e-02  schwann   CLIC4
VIM6    8.849336e-06    1.638765  0.923  0.504  2.654801e-02  schwann     VIM
PEA153  1.025082e-05    3.333601  1.000  0.914  3.075246e-02  schwann   PEA15
SSH16   1.373332e-05    3.828819  1.000  0.851  4.119997e-02  schwann    SSH1
VGLL44  1.551995e-05    3.582362  0.615  0.444  4.655984e-02  schwann   VGLL4

[4003 rows x 7 columns]

In [ ]:
#Top 20 per cluster by log2FC
with conversion.localconverter(default_converter):
  %R top20 <- fDEGs %>% group_by(cluster) %>% arrange(desc(avg_log2FC), .by_group = TRUE) %>% slice_head(n = 20)

In [ ]:
%R top20

p_val  avg_log2FC  pct.1  pct.2     p_val_adj  cluster   gene
1    1.086253e-61    6.436757  0.811  0.726  3.258758e-58      PSC    LUM
2    7.607185e-53    6.141243  0.774  0.287  2.282156e-49      PSC   MMP2
3    6.263654e-59    6.115082  0.830  0.132  1.879096e-55      PSC    DCN
4    1.967602e-54    6.089565  0.811  0.731  5.902805e-51      PSC  THBS2
5    1.371164e-55    5.877843  1.000  0.275  4.113493e-52      PSC  SFRP2
..            ...         ...    ...    ...           ...      ...    ...
310  4.695867e-10    4.654715  0.615  0.294  1.408760e-06  schwann   NRP2
311  1.037683e-06    4.618638  1.000  0.966  3.113050e-03  schwann  ATOX1
312  1.836157e-08    4.345579  0.538  0.284  5.508471e-05  schwann  RASA3
313  8.739436e-07    4.289589  0.462  0.302  2.621831e-03  schwann  WIPF1
314  3.793447e-06    4.247407  0.385  0.133  1.138034e-02  schwann  MXRA8

[314 rows x 7 columns]

In [ ]:
%R gene_counts <- table(top20$gene)
%R exclusive_genes <- names(gene_counts[gene_counts == 1])

%R exclusive_top20 <- top20 %>% filter(gene %in% exclusive_genes)

p_val  avg_log2FC  pct.1  pct.2     p_val_adj  cluster   gene
1    6.263654e-59    6.115082  0.830  0.132  1.879096e-55      PSC    DCN
2    1.967602e-54    6.089565  0.811  0.731  5.902805e-51      PSC  THBS2
3    9.169066e-14    5.793356  0.415  0.286  2.750720e-10      PSC   MMP1
4    6.774042e-50    5.258102  0.830  0.133  2.032213e-46      PSC   THY1
5    2.156070e-48    4.870172  0.830  0.151  6.468210e-45      PSC   FMOD
..            ...         ...    ...    ...           ...      ...    ...
238  7.257347e-08    5.064614  0.538  0.302  2.177204e-04  schwann  HBEGF
239  1.405866e-12    5.024830  0.769  0.380  4.217599e-09  schwann   GPC1
240  4.695867e-10    4.654715  0.615  0.294  1.408760e-06  schwann   NRP2
241  1.037683e-06    4.618638  1.000  0.966  3.113050e-03  schwann  ATOX1
242  1.836157e-08    4.345579  0.538  0.284  5.508471e-05  schwann  RASA3

[242 rows x 7 columns]

In [ ]:
with conversion.localconverter(default_converter):
  %R -o fDEGs

In [ ]:
with conversion.localconverter(default_converter):
  %R -o exclusive_top20

In [ ]:
import pickle

# Save object to file
with open(out_path+"/DEGs.pkl", 'wb') as f:
    pickle.dump(fDEGs, f)

In [ ]:
with open(out_path+"/top20_exclusive.pkl", 'wb') as f:
    pickle.dump(exclusive_top20, f)

In [ ]:
with open(out_path+"/top5_exclusive.pkl", 'wb') as f:
    pickle.dump(top5_exclusive, f)

In [ ]:
fDEGs.to_csv(out_path+'/DEGs.tsv', index=False, sep='\t')

In [ ]:
exclusive_top20.to_csv(out_path+'/top20_exclusive.tsv', index=False, sep='\t')

In [ ]:
top5_exclusive.to_csv(out_path+'/top5_exclusive.tsv', index=False, sep='\t')

---------------------------------

In [ ]:
import pickle
with open(out_path+"/DEGs.pkl", 'rb') as f:
    DEGs  = pickle.load(f)

In [ ]:
import pickle
with open(out_path+"/top20_exclusive.pkl", 'rb') as f:
    exclusive_top20 = pickle.load(f)

In [ ]:
def violin_plot_one(X, y, top_markers, save_path):
    import pandas as pd, numpy as np, seaborn as sns, matplotlib.pyplot as plt, os

    # Combine expression + cell type
    data = X.assign(cell_type=y)

    # Flatten markers and keep only those present
    all_genes = top_markers.values.flatten()
    all_genes = [g for g in all_genes if g in data.columns]

    if not all_genes:
        raise ValueError("None of the top marker genes were found in the data columns!")

    # Determine subplot grid
    num_genes = len(all_genes)
    cols = 5
    rows = (num_genes + cols - 1) // cols

    fig, axes = plt.subplots(rows, cols, figsize=(30, rows * 5), sharey=True)
    axes = axes.flatten()

    for i, gene in enumerate(all_genes):
        sns.violinplot(
            x='cell_type', y=gene, hue='cell_type', data=data,
            ax=axes[i], palette='Set2', inner='quartile', legend=False
        )
        axes[i].set_title(gene, fontsize=10)
        axes[i].set_xlabel('')
        axes[i].tick_params(axis='x', rotation=45)

    # Hide unused axes
    for j in range(i+1, len(axes)):
        axes[j].axis('off')

    fig.text(0.01, 0.5, 'Gene Expression', ha='center', va='center', rotation='vertical', fontsize=14)
    fig.text(0.5, 0.04, 'Cell Type', ha='center', va='center', fontsize=14)
    fig.suptitle('Gene Expression Across Cell Types', fontsize=18)
    plt.tight_layout(rect=[0.03, 0.05, 1, 0.95])

    plt.savefig(save_path, format='svg')
    #plt.show()


In [ ]:
X = pd.DataFrame(adata.X,columns=adata.var['gene_ids'])
X

gene_ids        GCG        INS        TTR       IAPP     REG1A     CTRB2  \
0          3.205214  11.707858   5.499465   7.096131  3.088694  2.958193   
1          2.687733  13.350835   7.204935   9.587956  7.338157  3.144629   
2          4.425700  12.944847   7.021363  10.615623  3.400604  1.426852   
3          3.812242  12.769384   7.143592  10.124625  2.537718  1.426852   
4          3.389692  11.958689   6.727825  11.898273  2.059274  1.426852   
...             ...        ...        ...        ...       ...       ...   
14167     11.992407   4.943913  11.191292  -0.284349  1.798860  1.692734   
14168      6.785828   5.040039   6.447966   1.915922  3.082366  0.592349   
14169     11.727368   4.441873  12.292501   3.139193  0.419967  1.190694   
14170      7.180752   3.978094   6.752417   1.332705  2.306785 -0.890140   
14171      6.871437   2.361039   6.791162   1.056628  2.087295 -0.890140   

gene_ids     CTRB1       CHGB    CELA3A     PRSS1  ...      BIN1     CCDC9  \
0         1.023180   0.600822  0.959772  3.735772  ...  0.775485  0.082613   
1         2.139715   5.222132  3.417299  4.726946  ...  0.389067  0.082613   
2         1.023180   4.602549  0.959772  1.115506  ...  0.389067  0.082613   
3         1.023180   5.182094  0.959772  1.115506  ...  0.389067  0.082613   
4         1.023180   2.061743  0.959772  1.115506  ...  0.633647  0.082613   
...            ...        ...       ...       ...  ...       ...       ...   
14167     0.030632   9.268345  0.037254  2.207321  ...  2.629637  0.089417   
14168     0.030632   4.390702  0.037254 -0.375553  ...  2.247034  0.089417   
14169     0.030632  10.994401  0.037254  1.705281  ...  0.046763  0.089417   
14170     0.030632   2.794030  0.037254 -0.375553  ...  1.663818  0.089417   
14171     0.030632   3.273218  1.378231 -0.375553  ...  3.172226  0.089417   

gene_ids   PLEKHA5    MRPS16     CXADR    DHRS7B    PTGFRN    SEMA3B  \
0         0.478790  0.099732  0.255911  0.339283  0.055412  0.298933   
1         0.503119  0.571444  4.565206  3.564845  2.162279  0.298933   
2         0.357377  5.091532  4.900181  0.339283  0.055412  0.298933   
3         0.537054  0.885287  0.255911  0.339283  0.055412  0.298933   
4         2.555964  5.849941  0.255911  0.339283  0.055412  0.298933   
...            ...       ...       ...       ...       ...       ...   
14167     2.147373  2.845760  3.435381  2.465359  2.499974  0.108038   
14168     1.764771  2.941886 -0.567587 -0.117514  2.596100  0.108038   
14169     1.645334  3.164714 -0.567587 -0.117514 -0.082899  0.108038   
14170    -0.435500  0.262886  4.565479  2.735858  2.279735  0.108038   
14171    -0.435500  3.104709 -0.567587 -0.117514  3.042564  0.108038   

gene_ids    PNPLA2    ARRDC2  
0         1.581512  0.088518  
1         1.581512  0.088518  
2         1.581512  0.088518  
3         1.581512  1.145086  
4         1.581512  0.088518  
...            ...       ...  
14167    -1.068300  0.310000  
14168     1.131972  0.310000  
14169     1.012534  0.310000  
14170     1.785073  0.310000  
14171     2.499829  0.310000  

[14172 rows x 3000 columns]

In [ ]:
y = adata.obs['cell_type'].values
y

['beta', 'beta', 'beta', 'beta', 'beta', ..., 'alpha', 'mesenchymal', 'alpha', 'ductal', 'mesenchymal']
Length: 14172
Categories (16, object): ['PSC', 'acinar', 'activated_stellate', 'alpha', ..., 'mesenchymal',
                          'pp', 'quiescent_stellate', 'schwann']

In [ ]:
exclusive_top20['gene']

1        DCN
2      THBS2
3       MMP1
4       THY1
5       FMOD
       ...  
238    HBEGF
239     GPC1
240     NRP2
241    ATOX1
242    RASA3
Name: gene, Length: 242, dtype: object

In [ ]:
violin_plot_one(X,y,exclusive_top20['gene'],save_path=gdrivePath+"/Revision/DGE/violin_plot.svg")